# Exercise 1.1

In [1]:
import pandas as pd

d = pd.read_csv('GLT_filtered.csv')
d.head()

Date  AverageTemperature  AverageTemperatureUncertainty     City  \
0  1849-01-01              26.704                          1.435  Abidjan   
1  1849-02-01              27.434                          1.362  Abidjan   
2  1849-03-01                 NaN                            NaN  Abidjan   
3  1849-04-01              26.140                          1.387  Abidjan   
4  1849-05-01              25.427                          1.200  Abidjan   

         Country Latitude Longitude  
0  Côte D'Ivoire    5.63N     3.23W  
1  Côte D'Ivoire    5.63N     3.23W  
2  Côte D'Ivoire    5.63N     3.23W  
3  Côte D'Ivoire    5.63N     3.23W  
4  Côte D'Ivoire    5.63N     3.23W

In [2]:
import csv
import numpy as np

col_names = []
dataset = [[], [], [], [], [], [], []] 
with open('GLT_filtered.csv') as fp:
    reader = csv.reader(fp) 
    col_names = next(reader) 
    for cols in reader:
        if len(cols) == len(col_names): # every column must be present 
            for i in range(len(dataset)):
                dataset[i].append(cols[i])

In [3]:
for i in range(4):
    for j in range(len(dataset)):
        print(f'{dataset[j][i]} ', end='') 
        print('')

1849-01-01 
26.704 
1.435 
Abidjan 
CГґte D'Ivoire 
5.63N 
3.23W 
1849-02-01 
27.434 
1.3619999999999999 
Abidjan 
CГґte D'Ivoire 
5.63N 
3.23W 
1849-03-01 
 
 
Abidjan 
CГґte D'Ivoire 
5.63N 
3.23W 
1849-04-01 
26.14 
1.3869999999999998 
Abidjan 
CГґte D'Ivoire 
5.63N 
3.23W 


# Exercise 1.2

In [4]:
def count_missing(data):
    return sum([1 for d in data if d == ''])

count = len(dataset[1])
print(f'AverageTemperature, missing values out of the whole dataset: {100*count_missing(dataset[1])/count:.1f}%')
print(f'AverageTemperatureUncertainty, missing values out of the whole dataset: {100*count_missing(dataset[2])/count:.1f}%')

AverageTemperature, missing values out of the whole dataset: 12.6%
AverageTemperatureUncertainty, missing values out of the whole dataset: 12.6%


In [5]:
# find the index of the 'AverageTemperature' attribute
avg_temp_index = col_names.index('AverageTemperature')

# iterate over the 'AverageTemperature' column to fill missing values
for i in range(len(dataset[avg_temp_index])):
    if dataset[avg_temp_index][i] == '': # missing value found
        prev_value = None
        next_value = None
        for j in range(i-1, -1, -1): # search for closest antecedent value
            if dataset[avg_temp_index][j] != '':
                prev_value = float(dataset[avg_temp_index][j])
                break
        for j in range(i+1, len(dataset[avg_temp_index])): # search for closest successive value
            if dataset[avg_temp_index][j] != '':
                next_value = float(dataset[avg_temp_index][j])
                break
        if prev_value is None and next_value is None: # both antecedent and successive values are missing
            dataset[avg_temp_index][i] = 0 # assume 0 as the value for the missing value
        elif prev_value is None: # antecedent value is missing
            dataset[avg_temp_index][i] = (next_value + 0) / 2 # assume 0 as the antecedent value
        elif next_value is None: # successive value is missing
            dataset[avg_temp_index][i] = (prev_value + 0) / 2 # assume 0 as the successive value
        else: # both antecedent and successive values are present
            dataset[avg_temp_index][i] = (prev_value + next_value) / 2 # compute arithmetic mean

print(dataset[avg_temp_index]) # print the modified 'AverageTemperature' column

['26.704', '27.434', 26.787, '26.14', '25.427', '24.844', '24.058000000000003', '23.576', 24.4195, '25.263', '26.332', '25.45', '25.803', '27.89', '27.851999999999997', '26.547', '25.379', '24.903', '24.04000000000001', '23.758000000000006', '24.0', '24.491', '25.541999999999998', 26.4525, 26.90775, '27.363000000000003', '27.180999999999997', '26.604', 25.751, '24.898000000000003', '24.318', '23.752', '24.083000000000002', '25.138', 25.670500000000004, '26.203000000000007', 26.446000000000005, 26.567500000000003, 26.62825, 26.658625, 26.6738125, 26.681406250000002, 26.685203125, 26.6871015625, 26.68805078125, 26.688525390625, 26.688762695312498, 26.68888134765625, 26.688940673828125, 26.68897033691406, 26.68898516845703, 26.688992584228515, 26.688996292114258, 26.68899814605713, 26.688999073028565, 26.68899953651428, 26.68899976825714, 26.68899988412857, 26.688999942064285, 26.688999971032143, 26.68899998551607, 26.688999992758035, 26.688999996379017, 26.68899999818951, 26.688999999094

# Exercise 1.3

In [6]:
cities = set(dataset[3])
city_avg_temp = {}
city_avg_temp_unc = {}
for city in cities:
 idxs = [i for i, c in enumerate(dataset[3]) if c == city] # extract the indices
 city_avg_temp[city] = [dataset[1][i] for i in idxs]
 city_avg_temp_unc[city] = [dataset[2][i] for i in idxs] 

In [7]:
def print_top_n_temperatures(city, n, city_avg_temp):
    # Get the average temperature of the city
    avg_temp = city_avg_temp[city]
    if isinstance(avg_temp, list):
        avg_temp = sum([float(t) for t in avg_temp if isinstance(t, str)]) / len(avg_temp)
    print(f"Average temperature in {city}: {avg_temp:.2f} degrees")

    # Get the top N hottest and coldest temperatures
    sorted_temps = sorted([float(t) for t in city_avg_temp[city] if isinstance(t, str)])
    top_hottest = sorted_temps[-n:]
    top_coldest = sorted_temps[:n]

    # Print the top N hottest temperatures
    print(f"\nTop {n} hottest temperatures in {city}:")
    for i, temp in enumerate(top_hottest):
        print(f"{i+1}. {temp:.2f} degrees")

    # Print the top N coldest temperatures
    print(f"\nTop {n} coldest temperatures in {city}:")
    for i, temp in enumerate(top_coldest):
        print(f"{i+1}. {temp:.2f} degrees")

In [8]:
print_top_n_temperatures("Xian", 5, city_avg_temp)
print()
print_top_n_temperatures("Abidjan", 5, city_avg_temp)

Average temperature in Xian: 10.53 degrees

Top 5 hottest temperatures in Xian:
1. 26.41 degrees
2. 26.54 degrees
3. 26.66 degrees
4. 26.74 degrees
5. 26.76 degrees

Top 5 coldest temperatures in Xian:
1. -6.42 degrees
2. -5.57 degrees
3. -5.48 degrees
4. -5.42 degrees
5. -5.39 degrees

Average temperature in Abidjan: 21.22 degrees

Top 5 hottest temperatures in Abidjan:
1. 29.41 degrees
2. 29.47 degrees
3. 29.48 degrees
4. 29.60 degrees
5. 29.92 degrees

Top 5 coldest temperatures in Abidjan:
1. 22.36 degrees
2. 22.38 degrees
3. 22.53 degrees
4. 22.63 degrees
5. 22.64 degrees


# Exercise 2.1

In [9]:
from collections import Counter

reviews, labels = [], []

# use the UTF-8 encoding to read the file
with open('aclimdb_reviews_train.txt', encoding='utf-8') as fp:
    reader = csv.reader(fp)
    next(reader) # skip the header
    for row in reader:
        reviews.append(row[0])
        labels.append(row[1])

# print the first 10 reviews and their labels
for review, label in zip(reviews[:10], labels[:10]):
    print(f"Review: {review}\nLabel: {label}\n")

Review: For a movie that gets no respect there sure are a lot of memorable quotes listed for this gem. Imagine a movie where Joe Piscopo is actually funny! Maureen Stapleton is a scene stealer. The Moroni character is an absolute scream. Watch for Alan "The Skipper" Hale jr. as a police Sgt.
Label: 1

Review: Working with one of the best Shakespeare sources, this film manages to be creditable to it's source, whilst still appealing to a wider audience.<br /><br />Branagh steals the film from under Fishburne's nose, and there's a talented cast on good form.
Label: 0

Review: Bizarre horror movie filled with famous faces but stolen by Cristina Raines (later of TV's "Flamingo Road") as a pretty but somewhat unstable model with a gummy smile who is slated to pay for her attempted suicides by guarding the Gateway to Hell! The scenes with Raines modeling are very well captured, the mood music is perfect, Deborah Raffin is charming as Cristina's pal, but when Raines moves into a creepy Brookly

# Exercise 2.2

In [10]:
import string

def tokenize(docs):
    """Compute the tokens for each document.
    Input: a list of strings. Each item is a document to tokenize.
    Output: a list of lists. Each item is a list containing the tokens of the
    relative document.
    """
    tokens = []
    for doc in docs:
        for punct in string.punctuation:
            doc = doc.replace(punct, " ")
        split_doc = [token.lower() for token in doc.split(" ") if token]
        tokens.append(split_doc)

    return tokens

reviews_tokenized = tokenize(reviews)

In [11]:
def print_tokenized_reviews(tokenized_reviews):
    for i, review in enumerate(tokenized_reviews[:10]):
        print(f"Review {i + 1}:")
        print(review)
        print()
        
print_tokenized_reviews(reviews_tokenized)

Review 1:
['for', 'a', 'movie', 'that', 'gets', 'no', 'respect', 'there', 'sure', 'are', 'a', 'lot', 'of', 'memorable', 'quotes', 'listed', 'for', 'this', 'gem', 'imagine', 'a', 'movie', 'where', 'joe', 'piscopo', 'is', 'actually', 'funny', 'maureen', 'stapleton', 'is', 'a', 'scene', 'stealer', 'the', 'moroni', 'character', 'is', 'an', 'absolute', 'scream', 'watch', 'for', 'alan', 'the', 'skipper', 'hale', 'jr', 'as', 'a', 'police', 'sgt']

Review 2:
['working', 'with', 'one', 'of', 'the', 'best', 'shakespeare', 'sources', 'this', 'film', 'manages', 'to', 'be', 'creditable', 'to', 'it', 's', 'source', 'whilst', 'still', 'appealing', 'to', 'a', 'wider', 'audience', 'br', 'br', 'branagh', 'steals', 'the', 'film', 'from', 'under', 'fishburne', 's', 'nose', 'and', 'there', 's', 'a', 'talented', 'cast', 'on', 'good', 'form']

Review 3:
['bizarre', 'horror', 'movie', 'filled', 'with', 'famous', 'faces', 'but', 'stolen', 'by', 'cristina', 'raines', 'later', 'of', 'tv', 's', 'flamingo', 'road'

# Exercise 2.3

In [12]:
def compute_tf(reviews):
    """
    Compute the term frequency (TF) for each token in each document.
    Input: a list of lists. Each list contains the tokens of a single document.
    Output: a list of dictionaries. Each dictionary represents the term frequency
    of a single document. The keys of the dictionary are the unique tokens, and the
    values are the frequency of the corresponding token in the document.
    """
    tf_list = []
    for doc in reviews:
        tf_dict = {}
        for token in doc:
            if token in tf_dict:
                tf_dict[token] += 1
            else:
                tf_dict[token] = 1
        tf_list.append(tf_dict)
    return tf_list

In [13]:
for i, doc_tokens in enumerate(reviews_tokenized):
    doc_tf = {}
    for token in doc_tokens:
        if token in doc_tf:
            doc_tf[token] += 1
        else:
            doc_tf[token] = 1
    print(f"{doc_tf}\n")

{'for': 3, 'a': 5, 'movie': 2, 'that': 1, 'gets': 1, 'no': 1, 'respect': 1, 'there': 1, 'sure': 1, 'are': 1, 'lot': 1, 'of': 1, 'memorable': 1, 'quotes': 1, 'listed': 1, 'this': 1, 'gem': 1, 'imagine': 1, 'where': 1, 'joe': 1, 'piscopo': 1, 'is': 3, 'actually': 1, 'funny': 1, 'maureen': 1, 'stapleton': 1, 'scene': 1, 'stealer': 1, 'the': 2, 'moroni': 1, 'character': 1, 'an': 1, 'absolute': 1, 'scream': 1, 'watch': 1, 'alan': 1, 'skipper': 1, 'hale': 1, 'jr': 1, 'as': 1, 'police': 1, 'sgt': 1}

{'working': 1, 'with': 1, 'one': 1, 'of': 1, 'the': 2, 'best': 1, 'shakespeare': 1, 'sources': 1, 'this': 1, 'film': 2, 'manages': 1, 'to': 3, 'be': 1, 'creditable': 1, 'it': 1, 's': 3, 'source': 1, 'whilst': 1, 'still': 1, 'appealing': 1, 'a': 2, 'wider': 1, 'audience': 1, 'br': 2, 'branagh': 1, 'steals': 1, 'from': 1, 'under': 1, 'fishburne': 1, 'nose': 1, 'and': 1, 'there': 1, 'talented': 1, 'cast': 1, 'on': 1, 'good': 1, 'form': 1}

{'bizarre': 1, 'horror': 1, 'movie': 2, 'filled': 1, 'with':

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



{'jessica': 2, 'a': 15, 'ghost': 3, 'story': 3, 'is': 7, 'as': 5, 'the': 26, 'name': 2, 'implies': 1, 'theme': 1, 'meant': 1, 'to': 11, 'be': 2, 'horror': 2, 'but': 1, 'comes': 3, 'across': 2, 'closer': 1, 'comedy': 1, 'br': 12, 'woman': 2, 'who': 3, 'was': 1, 'brutally': 1, 'murdered': 1, 'back': 1, 'from': 2, 'dead': 1, 'this': 7, 'constitutes': 1, 'what': 1, 'movie': 7, 'attempts': 1, 'pass': 1, 'off': 1, 'plot': 1, 'there': 1, 'really': 1, 'nothing': 1, 'more': 2, 'it': 3, 'comprises': 1, 'of': 13, 'series': 1, 'loosely': 1, 'connected': 1, 'scenes': 3, 'involving': 1, 'guy': 1, 'had': 3, 'an': 1, 'affair': 1, 'with': 5, 'prior': 1, 'her': 1, 'death': 1, 'immediately': 1, 'opening': 1, 'has': 3, 'appearance': 1, 'straight': 2, 'dvd': 2, 'effort': 1, 'unlike': 1, 'gems': 1, 'such': 1, 'vacancy': 1, '2': 2, 'no': 2, 'sense': 1, 'direction': 2, 'or': 4, 'creativity': 1, 'and': 2, 'certainly': 1, 'gives': 1, 'movies': 3, 'bad': 2, 'poor': 2, 'can': 1, 'complete': 1, 'lack': 1, 'suspens

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



# Exercise 2.4 

In [14]:
df = {}
for doc_tokens in reviews_tokenized:
    for token in set(doc_tokens):
        df[token] = df.get(token, 0) + 1

In [15]:
import math

idf = {}
N = len(reviews_tokenized)
for token in df:
    idf[token] = math.log(N / df[token])

In [16]:
sorted_idf = sorted(idf.items(), key=lambda x: x[1])
print(sorted_idf[:10])

[('the', 0.008314469604085238), ('a', 0.03351541933781697), ('and', 0.03401190259170586), ('of', 0.05226218466281087), ('to', 0.06293979977387414), ('this', 0.09924591465797242), ('is', 0.1086102347240488), ('it', 0.11536595914077863), ('in', 0.12606221366364628), ('that', 0.20722099077039452)]


# Exercise 2.5